In [3]:
import pymongo
import pandas as pd
from pandas import Series,DataFrame
import matplotlib as plt
import matplotlib.dates as mdate
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
#二行即可搞定画图中文乱码
plt.rcParams['font.sans-serif']=['SimHei'] #用来正常显示中文标签
plt.rcParams['axes.unicode_minus']=False #用来正常显示负号
pd.set_option('display.width', None)  # 设置字符显示宽度
pd.set_option('display.max_rows', None)  # 设置显示最大行
pd.set_option('display.max_columns', None)  # 设置显示最大行

#连接数据库
client = pymongo.MongoClient('localhost',27017)
futures = client.futures
market = futures.market
unit = futures.unit
position = futures.position


#加载数据
market = DataFrame(list(market.find()))
unit = DataFrame(list(unit.find()))
position = DataFrame(list(position.find()))

#列名重名
position= position.rename(columns={'var':'variety'})

#删除/选取某行含有特殊数值的列

position=position.dropna()

# ##选择需要显示的字段
marketdata=market[['variety','date','change']]
position=position[['date','variety','symbol','long_openIntr','short_openIntr']]

#修改日期格式，非常方便
marketdata['date'] = pd.to_datetime(marketdata['date'], format='%Y/%m/%d')
position['date'] = pd.to_datetime(position['date'], format='%Y/%m/%d')
# 值替换replace()
# position=position.replace(['PTA'],'TA')
#汇总合约
netPosition=position.groupby(['date','variety'])[['long_openIntr','short_openIntr']].sum()

netPosition['净持仓']=netPosition.apply(lambda x:x['long_openIntr']-x['short_openIntr'],axis=1)
netPosition['上一日净持仓']=netPosition.groupby('variety')['净持仓'].shift(1)
netPosition['净持仓变化量']=netPosition.apply(lambda x: x['净持仓']-x['上一日净持仓'],axis=1)
netPosition=netPosition.dropna()

marketdata.set_index(['date','variety'])
#计算价格变化量



trade=pd.merge(netPosition,marketdata, on=['date','variety'],how='outer')
trade
# trade['净持仓变化量'].corr(trade['change'])

D:\Anaconda3\lib\site-packages\ipykernel_launcher.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


date variety  long_openIntr  short_openIntr       净持仓    上一日净持仓  \
0     2018-04-10       A        87606.0        103538.0  -15932.0  -21032.0   
1     2018-04-10      AG       249916.0        254001.0   -4085.0   -7516.0   
2     2018-04-10      AL       257039.0        296998.0  -39959.0  -41884.0   
3     2018-04-10      AP        36056.0         32587.0    3469.0    1248.0   
4     2018-04-10      AU        94792.0         30458.0   64334.0   65115.0   
5     2018-04-10       B        26040.0         28173.0   -2133.0   -1663.0   
6     2018-04-10      BU       152963.0        141957.0   11006.0    9954.0   
7     2018-04-10       C       469152.0        590589.0 -121437.0 -131361.0   
8     2018-04-10      CF       157540.0        180497.0  -22957.0  -21981.0   
9     2018-04-10      CS       125589.0        118937.0    6652.0   -1421.0   
10    2018-04-10      CU       264319.0        287791.0  -23472.0  -23741.0   
11    2018-04-10      CY           18.0            18.0       0.0       0.0   
12    2018-04-10      ER            4.0             4.0       0.0       0.0   
13    2018-04-10      FG       103072.0         98974.0    4098.0    4768.0   
14    2018-04-10      HC       186911.0        183144.0    3767.0    1807.0   
15    2018-04-10       I       776291.0        854382.0  -78091.0  -81824.0   
16    2018-04-10      IC        24379.0         24186.0     193.0     156.0   
17    2018-04-10      IF        27492.0         30459.0   -2967.0   -3160.0   
18    2018-04-10      IH        11947.0         13807.0   -1860.0   -1876.0   
19    2018-04-10       J        94521.0         94839.0    -318.0    -150.0   
20    2018-04-10      JD        43515.0         40452.0    3063.0    2515.0   
21    2018-04-10      JM        89159.0         89579.0    -420.0    2356.0   
22    2018-04-10      JR           49.0            49.0       0.0       0.0   
23    2018-04-10       L       151833.0        173667.0  -21834.0  -21775.0   
24    2018-04-10       M      1135661.0       1458030.0 -322369.0 -273243.0   
25    2018-04-10      MA       249529.0        236904.0   12625.0   17566.0   
26    2018-04-10      NI       222232.0        221329.0     903.0   -2437.0   
27    2018-04-10      OI       142418.0        182528.0  -40110.0  -40089.0   
28    2018-04-10       P       150585.0        199941.0  -49356.0  -40572.0   
29    2018-04-10      PB        19089.0         18344.0     745.0     601.0   
30    2018-04-10      PM            3.0             3.0       0.0       0.0   
31    2018-04-10      PP       182541.0        157456.0   25085.0   27372.0   
32    2018-04-10      RB      1049307.0       1010171.0   39136.0   30728.0   
33    2018-04-10      RM       281569.0        320590.0  -39021.0  -36789.0   
34    2018-04-10      RS           11.0            11.0       0.0       0.0   
35    2018-04-10      RU       143543.0        192767.0  -49224.0  -49606.0   
36    2018-04-10      SF        68009.0         88825.0  -20816.0  -15308.0   
37    2018-04-10      SM        50395.0         51661.0   -1266.0     698.0   
38    2018-04-10      SN         7233.0          7095.0     138.0     390.0   
39    2018-04-10      SR       215569.0        245882.0  -30313.0  -34699.0   
40    2018-04-10       T        35794.0         37564.0   -1770.0   -2393.0   
41    2018-04-10      TA       558615.0        596022.0  -37407.0  -27799.0   
42    2018-04-10      TF        17081.0         18432.0   -1351.0   -1471.0   
43    2018-04-10       V       111222.0        114572.0   -3350.0   -2643.0   
44    2018-04-10      WH          825.0          1027.0    -202.0    -201.0   
45    2018-04-10       Y       273265.0        427658.0 -154393.0 -134154.0   
46    2018-04-10      ZC       173595.0        162309.0   11286.0   15758.0   
47    2018-04-10      ZN       155979.0        142058.0   13921.0   13308.0   
48    2018-04-11       A        87935.0        104930.0  -16995.0  -15932.0   
49    2018-04-11      AG       253016.0        248281.0    473